## summary

* 2.5d segmentation
    *  segmentation_models_pytorch 
    *  Unet
* use only 6 slices in the middle
* slide inference

In [1]:

from sklearn.metrics import roc_auc_score, accuracy_score, f1_score, log_loss
import pickle
from torch.utils.data import DataLoader
from torch.cuda.amp import autocast, GradScaler
import warnings
import sys
import pandas as pd
import os
import gc
import sys
import math
import time
import random
import shutil
from pathlib import Path
from contextlib import contextmanager
from collections import defaultdict, Counter
import cv2

import scipy as sp
import numpy as np
import pandas as pd

import matplotlib.pyplot as plt
from tqdm.auto import tqdm
from functools import partial

import argparse
import importlib
import torch
import torch.nn as nn
from torch.optim import Adam, SGD, AdamW

import torch
import torch.nn as nn
import torch.nn.functional as F
from functools import partial


import datetime

In [2]:
# sys.path.append('/kaggle/input/pretrainedmodels/pretrainedmodels-0.7.4')
# sys.path.append('/kaggle/input/efficientnet-pytorch/EfficientNet-PyTorch-master')
# sys.path.append('/kaggle/input/timm-pytorch-image-models/pytorch-image-models-master')
# sys.path.append('/kaggle/input/segmentation-models-pytorch/segmentation_models.pytorch-master')

In [3]:
import sys

sys.path.append("/home/viktor/Documents/kaggle/vesuvius-challenge/experiments/2.5d-segmentaion-baseline-[training]/exp-5-resnet34/resnet34-fold-1/resnet3d")
from resnet3d import generate_model

In [4]:
import segmentation_models_pytorch as smp

In [5]:
import numpy as np
from torch.utils.data import DataLoader, Dataset
import cv2
import torch
import os
import albumentations as A
from albumentations.pytorch import ToTensorV2
from albumentations import ImageOnlyTransform

## config

In [6]:
import os
import albumentations as A
from albumentations.pytorch import ToTensorV2

class CFG:
    # ============== comp exp name =============
    comp_name = 'vesuvius'

    # comp_dir_path = './'
    comp_dir_path = '/home/viktor/Documents/kaggle/vesuvius-challenge/kaggle-data/'
    comp_folder_name = 'vesuvius-challenge-ink-detection'
    # comp_dataset_path = f'{comp_dir_path}datasets/{comp_folder_name}/'
    comp_dataset_path = f'{comp_dir_path}{comp_folder_name}/'
    
    exp_name = 'vesuvius_2d_slide_exp002'

    # ============== pred target =============
    target_size = 1

    # ============== model cfg =============
    model_name = 'Unet'
    # backbone = 'efficientnet-b0'
    # backbone = 'se_resnext50_32x4d'
    backbone = 'resnet3d'

    in_chans = 16 # 65
    # ============== training cfg =============
    size = 2048
    tile_size = 2048
    stride = tile_size // 2
    
    kernel_size_image = 8 # from size to size / kernel_size_image
    kernel_size_target = 32 # from size to size / kernel_size_target

    train_batch_size = 32 # 32
    valid_batch_size = train_batch_size
    use_amp = True

    scheduler = 'GradualWarmupSchedulerV2'
    # scheduler = 'CosineAnnealingLR'
    epochs = 200 # 30

    # adamW warmupあり
    warmup_factor = 10
    # lr = 1e-4 / wsegarmup_factor
    lr = 1e-4 # / warmup_factor

    # ============== fold =============
    valid_id = 1

    # objective_cv = 'binary'  # 'binary', 'multiclass', 'regression'
    metric_direction = 'maximize'  # maximize, 'minimize'
    # metrics = 'dice_coef'

    # ============== fixed =============
    pretrained = True
    inf_weight = 'best'  # 'best'

    min_lr = 1e-6
    weight_decay = 1e-6
    max_grad_norm = 1000

    print_freq = 50
    num_workers = 4

    seed = 42
    
    # ==================== SWA ====================
    
    swa_start = 75
    swa_freq = 1
    swa_lr = 0.05

    # ============== set dataset path =============
    print('set dataset path')

    outputs_path = f'./{comp_name}/{exp_name}/'

    submission_dir = outputs_path + 'submissions/'
    submission_path = submission_dir + f'submission_{exp_name}.csv'

    model_dir = outputs_path + \
        f'{comp_name}-models/'

    figures_dir = outputs_path + 'figures/'

    log_dir = outputs_path + 'logs/'
    log_path = log_dir + f'{exp_name}.txt'

    # ============== augmentation =============
    train_aug_list = [
        # A.RandomResizedCrop(
        #     size, size, scale=(0.85, 1.0)),
        A.Resize(size, size),
        A.HorizontalFlip(p=0.5),
        A.VerticalFlip(p=0.5),
        A.RandomBrightnessContrast(p=0.75),
        A.ShiftScaleRotate(p=0.75),
        A.Rotate(limit=90, p=0.9), 
        A.OneOf([
                A.GaussNoise(var_limit=[10, 50]),
                A.GaussianBlur(),
                A.MotionBlur(),
                ], p=0.4),
        A.GridDistortion(num_steps=5, distort_limit=0.3, p=0.5),
        A.CoarseDropout(max_holes=1, max_width=int(size * 0.1), max_height=int(size * 0.1), 
                        mask_fill_value=0, p=0.5),
        # A.Cutout(max_h_size=int(size * 0.6),
        #          max_w_size=int(size * 0.6), num_holes=1, p=1.0),
        A.Normalize(
            mean= [0] * in_chans,
            std= [1] * in_chans
        ),
        ToTensorV2(transpose_mask=True),
    ]

    valid_aug_list = [
        A.Resize(size, size),
        A.Normalize(
            mean= [0] * in_chans,
            std= [1] * in_chans
        ),
        ToTensorV2(transpose_mask=True),
    ]


set dataset path


## helper

In [7]:
class AverageMeter(object):
    """Computes and stores the average and current value"""

    def __init__(self):
        self.reset()

    def reset(self):
        self.val = 0
        self.avg = 0
        self.sum = 0
        self.count = 0

    def update(self, val, n=1):
        self.val = val
        self.sum += val * n
        self.count += n
        self.avg = self.sum / self.count

In [8]:
def init_logger(log_file):
    from logging import getLogger, INFO, FileHandler, Formatter, StreamHandler
    logger = getLogger(__name__)
    logger.setLevel(INFO)
    handler1 = StreamHandler()
    handler1.setFormatter(Formatter("%(message)s"))
    handler2 = FileHandler(filename=log_file)
    handler2.setFormatter(Formatter("%(message)s"))
    logger.addHandler(handler1)
    logger.addHandler(handler2)
    return logger

def set_seed(seed=None, cudnn_deterministic=True):
    if seed is None:
        seed = 42

    os.environ['PYTHONHASHSEED'] = str(seed)
    np.random.seed(seed)
    random.seed(seed)
    torch.manual_seed(seed)
    torch.cuda.manual_seed(seed)
    torch.backends.cudnn.deterministic = cudnn_deterministic
    torch.backends.cudnn.benchmark = False

In [9]:
def make_dirs(cfg):
    for dir in [cfg.model_dir, cfg.figures_dir, cfg.submission_dir, cfg.log_dir]:
        os.makedirs(dir, exist_ok=True)

In [10]:
def cfg_init(cfg, mode='train'):
    set_seed(cfg.seed)
    # set_env_name()
    # set_dataset_path(cfg)

    if mode == 'train':
        make_dirs(cfg)

In [11]:
cfg_init(CFG)

device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')

Logger = init_logger(log_file=CFG.log_path)

Logger.info('\n\n-------- exp_info -----------------')
# Logger.info(datetime.datetime.now().strftime('%Y年%m月%d日 %H:%M:%S'))



-------- exp_info -----------------


## image, mask

In [12]:
def read_image_mask(fragment_id):
    
    images = []

    # idxs = range(65)
    mid = 65 // 2
    start = mid - CFG.in_chans // 2
    end = mid + CFG.in_chans // 2
    idxs = range(start, end)

    for i in tqdm(idxs):
        
        image = cv2.imread(CFG.comp_dataset_path + f"train/{fragment_id}/surface_volume/{i:02}.tif", 0)

        pad0 = (CFG.tile_size - image.shape[0] % CFG.tile_size)
        pad1 = (CFG.tile_size - image.shape[1] % CFG.tile_size)

        image = np.pad(image, [(0, pad0), (0, pad1)], constant_values=0)

        images.append(image)
    images = np.stack(images, axis=2)

    mask = cv2.imread(CFG.comp_dataset_path + f"train/{fragment_id}/inklabels.png", 0)
    mask = np.pad(mask, [(0, pad0), (0, pad1)], constant_values=0)

    mask = mask.astype('float32')
    mask /= 255.0
    
    return images, mask

In [13]:
# def read_image_mask(fragment_id):
    
#     images = []
    
    
#     # take CFG.in_chans random idxs
#     idxs = np.random.choice(range(65), CFG.in_chans, replace=False)

#     for i in tqdm(idxs):
        
#         img_path = CFG.comp_dataset_path + f"train/{fragment_id}/surface_volume/{i:02}.tif"
#         print(img_path)
        
#         image = cv2.imread(img_path, 0)

#         pad0 = (CFG.tile_size - image.shape[0] % CFG.tile_size)
#         pad1 = (CFG.tile_size - image.shape[1] % CFG.tile_size)

#         image = np.pad(image, [(0, pad0), (0, pad1)], constant_values=0)

#         images.append(image)
#     images = np.stack(images, axis=2)

#     mask = cv2.imread(CFG.comp_dataset_path + f"train/{fragment_id}/inklabels.png", 0)
#     mask = np.pad(mask, [(0, pad0), (0, pad1)], constant_values=0)

#     mask = mask.astype('float32')
#     mask /= 255.0
    
#     return images, mask

In [14]:
def get_train_valid_dataset():
    train_images = []
    train_masks = []

    valid_images = []
    valid_masks = []
    valid_xyxys = []

    for fragment_id in range(1, 4):

        image, mask = read_image_mask(fragment_id)

        x1_list = list(range(0, image.shape[1]-CFG.tile_size+1, CFG.stride))
        y1_list = list(range(0, image.shape[0]-CFG.tile_size+1, CFG.stride))

        for y1 in y1_list:
            for x1 in x1_list:
                y2 = y1 + CFG.tile_size
                x2 = x1 + CFG.tile_size
                # xyxys.append((x1, y1, x2, y2))
        
                image_sub = image[y1:y2, x1:x2]
                mask_sub = mask[y1:y2, x1:x2, None]
                
                # if there is less then 10% of ink in the tile, skip it
                if np.sum(mask_sub) < 0.2 * CFG.tile_size * CFG.tile_size:
                    continue
                
                if fragment_id == CFG.valid_id:
                    valid_images.append(image_sub)
                    valid_masks.append(mask_sub)

                    valid_xyxys.append([x1, y1, x2, y2])
                else:
                    train_images.append(image_sub)
                    train_masks.append(mask_sub)

    return train_images, train_masks, valid_images, valid_masks, valid_xyxys

In [15]:
train_images, train_masks, valid_images, valid_masks, valid_xyxys = get_train_valid_dataset()

  0%|          | 0/16 [00:00<?, ?it/s]

  0%|          | 0/16 [00:00<?, ?it/s]

In [16]:
valid_xyxys = np.stack(valid_xyxys)

## dataset

In [17]:
import numpy as np
from torch.utils.data import DataLoader, Dataset
import cv2
import torch
import os
import albumentations as A
from albumentations.pytorch import ToTensorV2
from albumentations import ImageOnlyTransform

In [18]:
def get_transforms(data, cfg):
    if data == 'train':
        aug = A.Compose(cfg.train_aug_list)
    elif data == 'valid':
        aug = A.Compose(cfg.valid_aug_list)

    # print(aug)
    return aug

class CustomDataset(Dataset):
    def __init__(self, images, cfg, labels=None, transform=None):
        self.images = images
        self.cfg = cfg
        self.labels = labels
        self.transform = transform

    def __len__(self):
        # return len(self.df)
        return len(self.images)

    def __getitem__(self, idx):
        image = self.images[idx]
        label = self.labels[idx]

        if self.transform:
            data = self.transform(image=image, mask=label)
            image = data['image']
            label = data['mask']
            
            
            image_2 = image.permute(2, 0, 1).unsqueeze(0)
            kernel = self.cfg.kernel_size_image
            kernel_size = (kernel, kernel)
            # Perform the average pooling with stride=32 to downsample the image by 32 and take the average across 32x32 pixels
            image_2 = torch.nn.functional.avg_pool2d(image_2, kernel_size=kernel_size, stride=kernel)
            
            # return to previous shape
            image = image.squeeze(0).permute(1, 2, 0)
            
            
            # Same for label
            label_2 = label.squeeze().unsqueeze(0).unsqueeze(0)
            kernel = self.cfg.kernel_size_target
            kernel_size = (kernel, kernel)
            # Perform the average pooling with stride=32 to downsample the image by 32 and take the average across 32x32 pixels
            label_2 = torch.nn.functional.avg_pool2d(label_2, kernel_size=kernel_size, stride=kernel)
            
            # return to previous shape
            label = label_2.squeeze(0) # 1, 256, 256
            
        # image = (image - 0.45)/0.225
        
        
        return image, label

In [19]:

train_dataset = CustomDataset(
    train_images, CFG, labels=train_masks, transform=get_transforms(data='train', cfg=CFG))
valid_dataset = CustomDataset(
    valid_images, CFG, labels=valid_masks, transform=get_transforms(data='valid', cfg=CFG))

train_loader = DataLoader(train_dataset,
                          batch_size=CFG.train_batch_size,
                          shuffle=True,
                          num_workers=CFG.num_workers, pin_memory=True, drop_last=True
                          )
valid_loader = DataLoader(valid_dataset,
                          batch_size=CFG.valid_batch_size,
                          shuffle=False,
                          num_workers=CFG.num_workers, pin_memory=True, drop_last=False)


In [20]:
train_dataset[0][0].max(), valid_dataset[0][0].max()

(tensor(1.), tensor(1.))

In [21]:
images=train_dataset[0][0].numpy()
print(images.shape)
np.min(images), np.max(images)

(2048, 2048, 16)


(0.0, 1.0)

In [ ]:
# valid_dataset[0][0].min(), valid_dataset[0][0].max()

In [ ]:

# plot_dataset = CustomDataset(
#     train_images, CFG, labels=train_masks)

# transform = CFG.train_aug_list
# transform = A.Compose(
#     [t for t in transform if not isinstance(t, (A.Normalize, ToTensorV2))])


# plot_count = 0
# for i in range(1000):

#     image, mask = plot_dataset[i]
#     data = transform(image=image, mask=mask)
#     aug_image = data['image']
#     aug_mask = data['mask']

#     if mask.sum() == 0:
#         continue

#     fig, axes = plt.subplots(1, 4, figsize=(15, 8))
#     axes[0].imshow(image[..., 0], cmap="gray")
#     axes[1].imshow(mask, cmap="gray")
#     axes[2].imshow(aug_image[..., 0], cmap="gray")
#     axes[3].imshow(aug_mask, cmap="gray")
    
#     plt.savefig(CFG.figures_dir + f'aug_fold_{CFG.valid_id}_{plot_count}.png')

#     plot_count += 1
#     if plot_count == 5:
#         break

In [ ]:
# del plot_dataset
# gc.collect()

## model

In [25]:
class Decoder(nn.Module):
    def __init__(self, encoder_dims, upscale):
        super().__init__()
        self.convs = nn.ModuleList([
            nn.Sequential(
                nn.Conv2d(encoder_dims[i]+encoder_dims[i-1], encoder_dims[i-1], 3, 1, 1, bias=False),
                nn.BatchNorm2d(encoder_dims[i-1]),
                nn.ReLU(inplace=True)
            ) for i in range(1, len(encoder_dims))])

        self.logit = nn.Conv2d(encoder_dims[0], 1, 1, 1, 0)
        self.up = nn.Upsample(scale_factor=upscale, mode="bilinear")

    def forward(self, feature_maps):
        for i in range(len(feature_maps)-1, 0, -1):
            f_up = F.interpolate(feature_maps[i], scale_factor=2, mode="bilinear")
            f = torch.cat([feature_maps[i-1], f_up], dim=1)
            f_down = self.convs[i-1](f)
            feature_maps[i-1] = f_down

        x = self.logit(feature_maps[0])
        mask = self.up(x)
        return mask
    
class SegModel(nn.Module):
    def __init__(self,model_depth=34):
        super().__init__()
        self.encoder = generate_model(model_depth=model_depth, n_input_channels=1)
        self.decoder = Decoder(encoder_dims=[64, 128, 256, 512], upscale=1)
        
    def forward(self, x):
        if x.ndim==4:
            x=x[:,None]
        
        feat_maps = self.encoder(x)
        feat_maps_pooled = [torch.mean(f, dim=2) for f in feat_maps]
        pred_mask = self.decoder(feat_maps_pooled)
        return pred_mask
    
class CustomModel(nn.Module):
    def __init__(self, cfg, weight=None):
        super().__init__()
        self.cfg = cfg
        if cfg.backbone=="resnet3d":
            self.encoder=SegModel()
        else:
            self.encoder = smp.Unet(
                encoder_name=cfg.backbone, 
                encoder_weights=weight,
                in_channels=cfg.in_chans,
                classes=cfg.target_size,
                activation=None,
            )

    def forward(self, image):
        output = self.encoder(image)
        # output = output.squeeze(-1)
        return output


def build_model(cfg, weight="imagenet"):
    print('model_name', cfg.model_name)
    print('backbone', cfg.backbone)

    model = CustomModel(cfg, weight)

    return model

## scheduler

In [26]:

import torch.nn as nn
import torch
import math
import time
import numpy as np
import torch

from torch.optim.lr_scheduler import CosineAnnealingWarmRestarts, CosineAnnealingLR, ReduceLROnPlateau
from warmup_scheduler import GradualWarmupScheduler


class GradualWarmupSchedulerV2(GradualWarmupScheduler):
    """
    https://www.kaggle.com/code/underwearfitting/single-fold-training-of-resnet200d-lb0-965
    """
    def __init__(self, optimizer, multiplier, total_epoch, after_scheduler=None):
        super(GradualWarmupSchedulerV2, self).__init__(
            optimizer, multiplier, total_epoch, after_scheduler)

    def get_lr(self):
        if self.last_epoch > self.total_epoch:
            if self.after_scheduler:
                if not self.finished:
                    self.after_scheduler.base_lrs = [
                        base_lr * self.multiplier for base_lr in self.base_lrs]
                    self.finished = True
                return self.after_scheduler.get_lr()
            return [base_lr * self.multiplier for base_lr in self.base_lrs]
        if self.multiplier == 1.0:
            return [base_lr * (float(self.last_epoch) / self.total_epoch) for base_lr in self.base_lrs]
        else:
            return [base_lr * ((self.multiplier - 1.) * self.last_epoch / self.total_epoch + 1.) for base_lr in self.base_lrs]

def get_scheduler(cfg, optimizer):
    scheduler_cosine = torch.optim.lr_scheduler.CosineAnnealingLR(
        optimizer, cfg.epochs, eta_min=1e-7)
    scheduler = GradualWarmupSchedulerV2(
        optimizer, multiplier=10, total_epoch=1, after_scheduler=scheduler_cosine)

    return scheduler

def scheduler_step(scheduler, avg_val_loss, epoch):
    scheduler.step(epoch)


In [27]:
model = build_model(CFG)
# model.to(device);

# optimizer = AdamW(model.parameters(), lr=CFG.lr)
# scheduler = get_scheduler(CFG, optimizer)

model_name Unet
backbone resnet3d


## loss

In [28]:

DiceLoss = smp.losses.DiceLoss(mode='binary')
BCELoss = smp.losses.SoftBCEWithLogitsLoss()

alpha = 0.5
beta = 1 - alpha
TverskyLoss = smp.losses.TverskyLoss(
    mode='binary', log_loss=False, alpha=alpha, beta=beta)

def criterion(y_pred, y_true):
    # return 0.5 * BCELoss(y_pred, y_true) + 0.5 * DiceLoss(y_pred, y_true)
    bce_loss =  BCELoss(y_pred, y_true)
    return bce_loss
    
    y_preds_probas = torch.sigmoid(y_pred)
    dxx = torch.pow(torch.roll(y_preds_probas, shifts=-1, dims=-1) - 2*y_preds_probas + torch.roll(y_preds_probas, shifts=1, dims=-2), 2)
    dyy = torch.pow(torch.roll(y_preds_probas, shifts=-1, dims=-2) - 2*y_preds_probas + torch.roll(y_preds_probas, shifts=1, dims=-2), 2)

    # Average over all pixels
    kin_energy = torch.mean(dxx + dyy)

    
    return bce_loss + kin_energy
    # return 0.5 * BCELoss(y_pred, y_true) + 0.5 * TverskyLoss(y_pred, y_true)

## train, val

In [29]:
def train_fn(train_loader, model, criterion, optimizer, device):
    model.train()

    scaler = GradScaler(enabled=CFG.use_amp)
    losses = AverageMeter()

    for step, (images, labels) in tqdm(enumerate(train_loader), total=len(train_loader)):
        images = images.to(device)
        labels = labels.to(device)
        batch_size = labels.size(0)

        with autocast(CFG.use_amp):
            y_preds = model(images)
            loss = criterion(y_preds, labels)

        losses.update(loss.item(), batch_size)
        scaler.scale(loss).backward()

        grad_norm = torch.nn.utils.clip_grad_norm_(
            model.parameters(), CFG.max_grad_norm)

        scaler.step(optimizer)
        scaler.update()
        optimizer.zero_grad()

    return losses.avg





def valid_fn(valid_loader, model, criterion, device, valid_xyxys, valid_mask_gt):
    mask_pred = np.zeros(valid_mask_gt.shape)
    mask_count = np.zeros(valid_mask_gt.shape)

    model.eval()
    losses = AverageMeter()

    for step, (images, labels) in tqdm(enumerate(valid_loader), total=len(valid_loader)):
        images = images.to(device)
        labels = labels.to(device)
        batch_size = labels.size(0)

        with torch.no_grad():
            y_preds = model(images)
            loss = criterion(y_preds, labels)
        losses.update(loss.item(), batch_size)

        # make whole mask
        y_preds = torch.sigmoid(y_preds).to('cpu').numpy()
        start_idx = step*CFG.valid_batch_size
        end_idx = start_idx + batch_size
        for i, (x1, y1, x2, y2) in enumerate(valid_xyxys[start_idx:end_idx]):
            mask_pred[y1:y2, x1:x2] += y_preds[i].squeeze(0)
            mask_count[y1:y2, x1:x2] += np.ones((CFG.tile_size, CFG.tile_size))

    print(f'mask_count_min: {mask_count.min()}')
    mask_pred /= mask_count
    return losses.avg, mask_pred

## metrics

In [30]:
from sklearn.metrics import fbeta_score

def fbeta_numpy(targets, preds, beta=0.5, smooth=1e-5):
    """
    https://www.kaggle.com/competitions/vesuvius-challenge-ink-detection/discussion/397288
    """
    y_true_count = targets.sum()
    ctp = preds[targets==1].sum()
    cfp = preds[targets==0].sum()
    beta_squared = beta * beta

    c_precision = ctp / (ctp + cfp + smooth)
    c_recall = ctp / (y_true_count + smooth)
    dice = (1 + beta_squared) * (c_precision * c_recall) / (beta_squared * c_precision + c_recall + smooth)

    return dice

def calc_fbeta(mask, mask_pred):
    mask = mask.astype(int).flatten()
    mask_pred = mask_pred.flatten()

    best_th = 0
    best_dice = 0
    for th in np.array(range(10, 100+1, 5)) / 100:
        
        # dice = fbeta_score(mask, (mask_pred >= th).astype(int), beta=0.5)
        dice = fbeta_numpy(mask, (mask_pred >= th).astype(int), beta=0.5)
        print(f'th: {th}, fbeta: {dice}')

        if dice > best_dice:
            best_dice = dice
            best_th = th
    
    Logger.info(f'best_th: {best_th}, fbeta: {best_dice}')
    return best_dice, best_th


def calc_cv(mask_gt, mask_pred):
    best_dice, best_th = calc_fbeta(mask_gt, mask_pred)

    return best_dice, best_th

## main

In [ ]:
fragment_id = CFG.valid_id

valid_mask_gt = cv2.imread(CFG.comp_dataset_path + f"train/{fragment_id}/inklabels.png", 0)
valid_mask_gt = valid_mask_gt / 255
pad0 = (CFG.tile_size - valid_mask_gt.shape[0] % CFG.tile_size)
pad1 = (CFG.tile_size - valid_mask_gt.shape[1] % CFG.tile_size)
valid_mask_gt = np.pad(valid_mask_gt, [(0, pad0), (0, pad1)], constant_values=0)

In [ ]:
optimizer = torch.optim.AdamW(model.parameters(), lr=CFG.lr)

In [ ]:
# custom implementation of torch.optim.swa_utils.update_bn(train_loader, swa_model)
def manual_update_bn(model):
    model.train()
    with torch.no_grad():  # deactivate autograd engine to reduce memory usage and speed up computations

        for step, (images, labels) in tqdm(enumerate(train_loader), total=len(train_loader)):
            images = images.to(device)
            _ = model(images)

In [ ]:
import copy

fold = CFG.valid_id

if CFG.metric_direction == 'minimize':
    best_score = np.inf
    best_score_swa = np.inf
elif CFG.metric_direction == 'maximize':
    best_score = -1
    best_score_swa = -1

best_loss = np.inf

swa_n = 0
for epoch in range(CFG.epochs):

    start_time = time.time()

    # train
    avg_loss = train_fn(train_loader, model, criterion, optimizer, device)

    # eval
    avg_val_loss, mask_pred = valid_fn(valid_loader, model, criterion, device, valid_xyxys, valid_mask_gt)
    if epoch > CFG.swa_start:
        avg_val_loss_swa, mask_pred_swa = valid_fn(valid_loader, swa_model, criterion, device, valid_xyxys, valid_mask_gt)

    # scheduler_step(scheduler, avg_val_loss, epoch)

    # get best dice and threshold for both models
    best_dice, best_th = calc_cv(valid_mask_gt, mask_pred)
    if epoch > CFG.swa_start:
        best_dice_swa, best_th_swa = calc_cv(valid_mask_gt, mask_pred_swa)

    # score = avg_val_loss
    score = best_dice
    if epoch > CFG.swa_start:
        score_swa = best_dice_swa

    # score = avg_val_loss
    score = best_dice

    elapsed = time.time() - start_time

    Logger.info(
        f'Epoch {epoch+1} - avg_train_loss: {avg_loss:.4f}  avg_val_loss: {avg_val_loss:.4f}  time: {elapsed:.0f}s')
    if epoch > CFG.swa_start:
        Logger.info(
            f'Epoch {epoch+1} - SWA avg_val_loss: {avg_val_loss_swa:.4f}  time: {elapsed:.0f}s')

    Logger.info(
        f'Epoch {epoch+1} - avgScore: {score:.4f}')
    if epoch > CFG.swa_start:
        Logger.info(
            f'Epoch {epoch+1} - SWA avgScore: {score_swa:.4f}')

    if CFG.metric_direction == 'minimize':
        update_best = score < best_score
        if epoch > CFG.swa_start:
            update_best_swa = score_swa < best_score_swa
    elif CFG.metric_direction == 'maximize':
        update_best = score > best_score
        if epoch > CFG.swa_start:
            update_best_swa = score_swa > best_score_swa

    if update_best:
        best_loss = avg_val_loss
        best_score = score

        Logger.info(
            f'Epoch {epoch+1} - Save Best Score: {best_score:.4f} Model')
        Logger.info(
            f'Epoch {epoch+1} - Save Best Loss: {best_loss:.4f} Model')
        
        torch.save({'model': model.state_dict(),
                    'preds': mask_pred},
                    CFG.model_dir + f'{CFG.model_name}_fold{fold}_best.pth')

    if epoch > CFG.swa_start and update_best_swa:
        best_loss_swa = avg_val_loss_swa
        best_score_swa = score_swa

        Logger.info(
            f'Epoch {epoch+1} - Save Best SWA Score: {best_score_swa:.4f} Model')
        Logger.info(
            f'Epoch {epoch+1} - Save Best SWA Loss: {best_loss_swa:.4f} Model')
        
        torch.save({'model': swa_model.state_dict(),
                    'preds': mask_pred_swa},
                    CFG.model_dir + f'{CFG.model_name}_fold{fold}_swa_best.pth')
        
    # update SWA after a certain number of epochs
    if epoch >= CFG.swa_start and epoch % CFG.swa_freq == 0:
        
        if epoch == CFG.swa_start:
            # duplicate model to swa_model
            swa_model = build_model(CFG).to(device)
            swa_n = 0  # to track the number of models used for averaging
            
            # copy weights from model
            swa_model.load_state_dict(model.state_dict())
            
            # switch to SGD optimizer 
            # optimizer = torch.optim.SGD(model.parameters(), lr=CFG.swa_lr)
            
            
        else:
            # loop over each parameter and update the swa_model parameter as average
            swa_n += 1
            for swa_param, param in zip(swa_model.parameters(), model.parameters()):
                swa_param.data.mul_(swa_n).add_(param.data).div_(swa_n + 1)
            
        



In [ ]:

# Update batch normalization for the SWA model before saving and/or evaluation
manual_update_bn(swa_model)       


# Finally, save the SWA model
torch.save({'model': swa_model.state_dict()},
            CFG.model_dir + f'{CFG.model_name}_fold{fold}_swa.pth')

In [ ]:
# mask_pred = check_point['preds']

In [ ]:
best_dice, best_th  = calc_fbeta(valid_mask_gt, mask_pred_swa)

In [ ]:
fig, axes = plt.subplots(1, 3, figsize=(15, 8))
axes[0].imshow(valid_mask_gt)
axes[1].imshow(mask_pred_swa)
axes[2].imshow((mask_pred_swa>=best_th).astype(int))

In [ ]:
plt.hist(mask_pred_swa.flatten(), bins=20)

In [ ]:
scores=[0.4600,
0.5090,
0.4911,
0.5214,
0.4640,
0.5301,
0.5474,
0.5470,
0.5667,
0.5449,
0.5772,
0.5385,
0.5655,
0.5854,
0.6025,
0.5639,
0.5629,
0.5602,
0.6078,
0.5806,
0.5465,
0.5669,
0.5854,
0.6025,
0.5863,
0.5759,
0.6124,
0.6088,
0.5758,
0.6207,
0.5808,
0.5937,
0.6136,
0.5989,
0.5640,
0.6039,
0.5857,
0.6083,
0.5937,
0.6014,
0.6204,
0.5989,
0.6015,
0.6073,
0.5772,
0.5966,
0.5697,
0.6169,
0.5766,
0.5875,
0.5668,
0.6199,
0.5953,
0.6256,
0.5851,
0.5363,
0.5765,
0.6051,
0.5922,
0.6293,
0.5816,
0.6179,
0.6330,
0.5828,
0.6175,
0.6377,
0.6112,
0.6084,
0.6494,
0.6371,
0.6219,
0.6347,
0.5920,
0.6054,
0.6014,
0.5988,
0.6496,
0.6168,
0.6259,
0.5733,
0.6196,
0.5635,
0.5979,
0.6064,
0.6184,
0.6232,
0.6003,
0.6400,
0.6145,
0.6341,
0.5803,
0.6113,
0.6053,
0.6109,
0.6572,
0.5985,
0.5926,
0.6180,
0.6088,
0.6271,
0.6453,
0.5769,
0.6376,
0.5935,
0.6027,
0.5877,
0.6227,
0.6289,
0.6032,
0.6104,
0.6297,
0.5969,
0.6313,
0.6198,
0.6296,
0.6224,
0.6489,
0.6049,
0.5877,
0.6044,
0.5912,
0.6321,
0.6091,
0.6216,
0.5878,
0.6127,
0.5709,
0.6049,
0.5916,
0.6218,
0.6392,
0.5949,
0.6169,
0.6212,
0.5576,
0.6265,
0.5649,
0.5627,
0.6098,
0.6225,
0.6114,
0.6192,
0.6281,
0.5815,
0.5957,
0.5789,
0.6271,
0.6181,
0.6284,
0.6116,
0.6135,
0.6078,
0.6066,
0.6074,
0.6105,
0.6070,
0.6105,
0.6099,
0.6038,
0.6037,
0.6058,
0.6078,
0.6125,
0.6113,
0.6125,
0.6124,
0.6113,
0.6130,
0.6144,
0.6134,
0.6090,
0.6081,
0.6099,
0.6093,
0.6120,
0.6173,
0.6107,
0.6125,
0.6146,
0.6123,
0.6138,
0.6129,
0.6092,
0.6096,
0.6113,
0.6173,
0.6084,
0.6164,
0.6121,
0.6177,
0.6155,
0.6164,
0.6175,
0.6139,
0.6178,
0.6188,
0.6141,
0.6119,
0.6164,
0.6157]

import matplotlib.pyplot as plt
plt.plot(scores)